## Домашнее задание

Основаная задача - **построить хорошую тематическую модель с интерпретируемыми топиками с помощью LDA в gensim и NMF в sklearn**.


1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор); 

2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

4) постройте несколько LDA моделей (переберите количество тем, можете поменять eta, alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы;

6) между словарем и обучением модели добавьте tfidf (`gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

7) повторите пункт 4 на преобразованном корпусе;

8) в отдельной ячейке опишите как изменилась модель (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

10) в отдельной ячейки напечатайте таблицу с темами лучшей NMF модели, сравните их с теми, что получились в LDA.

Сохраните тетрадку с экспериментами и положите её на гитхаб, ссылку на неё укажите в форме.

**Оцениваться будут главным образом пункты 5, 8 и 10. (2, 3, 2 баллов соответственно). Чтобы заработать остальные 3 балла, нужно хотя бы немного изменить мой код на промежуточных этапах (добавить что-то, указать другие параметры и т.д). **

In [1]:
import gensim
import json
import re
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer
import pyLDAvis.gensim
import string
from collections import Counter
import warnings
warnings.filterwarnings("ignore")

morph = MorphAnalyzer()

d:\python371\lib\site-packages\gensim\utils.py:1212: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


## Данные

Я добавила стоп-слова из английского и расширила их лексикой, которая встречается в коде, потому что такие слова не могут быть ключевыми.

In [37]:
rus = stopwords.words('russian') + ['который', 'это']
eng = stopwords.words('english') + ['end', 'char', 'return', 'int', 'else', 'null', 'var', 'string',\
                                   'static', 'class', 'function', 'bool', 'get', 'set', 'message']
stops = set(rus + eng)
# stops = set(stopwords.words('russian')) | {'gt',}

In [44]:
# stops = set(stopwords.words('russian').extend(stopwords.words('english'))) | {'gt',}
def remove_tags(text):
    return re.sub(r'<[^>]+>', '', text)

def normalize(words):
    norm_words = [morph.parse(word)[0].normal_form for word in words if len(set(word)) > 1]
    return norm_words

def opt_normalize(texts, top=None):
    uniq = Counter()
    for text in texts:
        uniq.update(text)
    
    norm_uniq = {word:morph.parse(word)[0].normal_form for word, _ in uniq.most_common(top)}
    
    norm_texts = []
    for text in texts:
        
        norm_words = [norm_uniq.get(word) for word in text]
        norm_words = [word for word in norm_words if word and word not in stops]
        norm_words = [word for word in norm_words if len(set(word)) > 1 and not word.isdigit()]  # удаляем числа
        norm_texts.append(norm_words)
        
    return norm_texts

def tokenize(text):
    words = [word.strip(string.punctuation) for word in text.split()]
    words = [word for word in words if word]
    
    return words

Возьмем 4 тыс статьи с Хабра. Это мало для хорошей тематической модели, но иначе у нас просто ничего не обучится за семинар.

In [8]:
habr_texts = opt_normalize([tokenize(remove_tags(text.lower())) for text in open('habr_texts.txt\\habr_texts.txt', encoding='utf-8')])

In [4]:
# I already have habr_texts.vw after implementing BigARTM
f = open('habr_texts.vw', 'w')
for i, text in enumerate(habr_texts):
    c = Counter(text)
    doc = 'doc_'+ str(i) + ' '
    vw_text = ' '.join([x+':'+str(c[x]) for x in c])
    f.write(doc + vw_text  + '\n')
f.close()

В текстах есть тэги. Потрем их. Ещё токенизируем самым простым способом и нормализуем Pymorphy.

In [44]:
%%time
texts = open('habr_texts.txt\\habr_texts.txt', encoding='utf-8').read().splitlines()
texts = [tokenize(remove_tags(text.lower())) for text in texts]

Wall time: 6.01 s


In [ ]:
%%time
texts = open('habr_texts.txt\\habr_texts.txt', encoding='utf-8').read().splitlines()
texts = [normalize(tokenize(text.lower())) for text in texts]

In [48]:
%%time
texts = open('habr_texts.txt\\habr_texts.txt', encoding='utf-8').read().splitlines()
texts = opt_normalize([tokenize(remove_tags(text.lower())) for text in texts], 30000)

Wall time: 20.7 s


In [ ]:
# для нграммов
# ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
# p = gensim.models.phrases.Phraser(ph)
# ngrammed_texts = p[texts]

### Тематическое моделирование в gensim

Для моделей нужно сделать словарь.

In [47]:
len(texts)

4121

In [46]:
texts[6]

['ошибка',
 'сложность',
 'столкнуться',
 'запускать',
 'собственный',
 'кластер',
 'база',
 'vmmanager',
 'cloud',
 'ceph',
 'предыстория',
 'приходить',
 'разный',
 'человек',
 'кто-то',
 'достаточно',
 'хостинг',
 'база',
 'cms',
 'кто-то',
 'виртуальный',
 'сервер',
 'человек',
 'просить',
 'производительный',
 'сервер',
 'повышенный',
 'сильно',
 'волновать',
 'стоимость',
 'услуга',
 'уверить',
 'наш',
 'обычный',
 'vds',
 'решить',
 'создать',
 'отдельный',
 'услуга',
 'высокий',
 'цена',
 'отказоустойчивость',
 'sla',
 'задача',
 'решаться',
 'создание',
 'кластер',
 'повышенный',
 'надёжность',
 'однако',
 'сомнение',
 'сетевой',
 'технология',
 'как-то',
 'собрать',
 'кластер',
 'сеть',
 'попробовать',
 'ничто',
 'выйти',
 'сеть',
 'кластер',
 'работать',
 'очень',
 'медленно',
 'использовать',
 'практический',
 'задача',
 'невозможно',
 'сложиться',
 'впечатление',
 'система',
 'уступать',
 'скорость',
 'классический',
 'решение',
 'знать',
 'технология',
 'infiniband',
 'го

In [8]:
# def remove_stopwords_en(texts):
#     return [[word for word in doc if word not in set(stopwords.words('english')) and not word.isdigit()] for doc in texts]

In [ ]:
# texts = remove_stopwords_en(texts)

In [ ]:
# def del_short(texts):
#     return [[word for word in words if len(set(word)) > 1 and not word.isdigit()] for doc in texts]

In [49]:
dictinary = gensim.corpora.Dictionary(texts)

Здесь я добавила параметр, чтобы как минимум в 5 документах встречалось слово из словаря и как максимум в 30% всех текстов.

In [50]:
dictinary.filter_extremes(no_below=5, no_above=0.3)  # min_tf=10, max_tf=2000, min_df_rate=0.01
dictinary.compactify()

In [51]:
print(dictinary)

Dictionary(11731 unique tokens: ['2-х', '3.0', 'address', 'api', 'architecture']...)


Преобразуем наши тексты в мешки слов. 

In [52]:
corpus = [dictinary.doc2bow(text) for text in texts]
# если текстов много, то тут может быть генератор

In [15]:
?gensim.models.LdaMulticore

In [53]:
%%time
lda = gensim.models.LdaMulticore(corpus, 100, id2word=dictinary, passes=5, eta='auto', iterations=10) # если поддерживается многопоточность
# lsi = gensim.models.LdaModel(200, id2word=dictinary, passes=5)

Wall time: 49.1 s


Посмотрим на топики.

In [54]:
lda.print_topics()

[(30,
  '0.012*"рубль" + 0.009*"скидка" + 0.008*"доход" + 0.007*"услуга" + 0.006*"налог" + 0.006*"сумма" + 0.006*"месяц" + 0.005*"бизнес" + 0.005*"деньга" + 0.005*"счёт"'),
 (73,
  '0.022*"research" + 0.013*"international" + 0.012*"ключ" + 0.011*"science" + 0.010*"publishing" + 0.009*"подпись" + 0.007*"scientific" + 0.007*"открытый" + 0.006*"журнал" + 0.005*"amp"'),
 (49,
  '0.008*"вселенная" + 0.007*"звезда" + 0.006*"галактика" + 0.006*"скорость" + 0.005*"объект" + 0.004*"земля" + 0.004*"её" + 0.004*"солнце" + 0.004*"энергия" + 0.004*"планета"'),
 (35,
  '0.012*"blackvue" + 0.009*"регистратор" + 0.007*"модель" + 0.006*"устройство" + 0.006*"программа" + 0.004*"видео" + 0.003*"память" + 0.003*"изображение" + 0.003*"computer" + 0.003*"модуль"'),
 (86,
  '0.011*"сигнал" + 0.008*"частота" + 0.006*"датчик" + 0.005*"мощность" + 0.005*"значение" + 0.004*"ток" + 0.004*"канал" + 0.004*"режим" + 0.003*"таймер" + 0.003*"параметр"'),
 (82,
  '0.012*"игра" + 0.006*"игрок" + 0.006*"технология" + 0.0

Ещё есть штука для визуализации.

In [55]:
pyLDAvis.enable_notebook()

In [56]:
pyLDAvis.gensim.prepare(lda, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
34    -0.138779 -0.008275       1        1  5.268044
32    -0.097087  0.080265       2        1  4.142146
9      0.155537 -0.044628       3        1  4.028040
77     0.160194  0.035391       4        1  3.859306
19    -0.096846  0.032224       5        1  3.808646
11     0.158737 -0.023672       6        1  3.789309
97     0.152319 -0.046946       7        1  3.134148
74    -0.051588  0.017676       8        1  3.043332
10    -0.071497 -0.015612       9        1  2.999254
90    -0.085236 -0.065726      10        1  2.923146
20    -0.021460  0.045906      11        1  2.838901
48     0.023191  0.089959      12        1  2.741986
5      0.094531  0.067078      13        1  2.668766
82    -0.102098 -0.031334      14        1  2.545733
49    -0.095181 -0.087367      15        1  2.494799
94     0.057139  0.062826      16        1  2.176351
80    -0.052114  0.050919      17        1  1.888939
60    -0.104091 -0.025241      18        1  1.855857
29    -0.042422 -0.072138      19        1  1.700420
66    -0.091069 -0.003976      20        1  1.682295
13     0.011248 -0.043270      21        1  1.634297
89    -0.071697  0.047556      22        1  1.577610
30    -0.090929  0.054149      23        1  1.540498
47     0.044545  0.030992      24        1  1.524186
18     0.130766  0.004476      25        1  1.505145
17     0.016935  0.019788      26        1  1.375033
92     0.030058 -0.026667      27        1  1.363084
84    -0.071326 -0.000465      28        1  1.304425
86     0.002308 -0.080246      29        1  1.143576
0     -0.052147  0.036618      30        1  1.034402
...         ...       ...     ...      ...       ...
53     0.005851  0.010770      71        1  0.257016
79     0.020202 -0.026897      72        1  0.247700
98    -0.001844  0.004229      73        1  0.238681
76    -0.053559  0.013811      74        1  0.230021
25    -0.016730  0.029854      75        1  0.226712
24     0.042685 -0.009787      76        1  0.224223
68    -0.002437  0.000504      77        1  0.211984
87    -0.038667  0.025734      78        1  0.208860
96     0.012690  0.002656      79        1  0.208809
44     0.023439 -0.032996      80        1  0.195173
4     -0.018620  0.000883      81        1  0.193870
85     0.017488  0.004286      82        1  0.171986
28    -0.020238  0.007904      83        1  0.168002
78     0.022648  0.005930      84        1  0.159463
58     0.020226 -0.009924      85        1  0.158591
63    -0.001819  0.004807      86        1  0.143390
65     0.044772 -0.011883      87        1  0.117177
54     0.002923  0.018095      88        1  0.115043
75     0.001367  0.006393      89        1  0.111950
99    -0.000647  0.006815      90        1  0.110571
39     0.005528  0.003515      91        1  0.101091
59     0.019069  0.001499      92        1  0.098504
22     0.018007 -0.007975      93        1  0.092320
2      0.017947 -0.010443      94        1  0.083285
93     0.016528 -0.018218      95        1  0.063042
3      0.012130  0.006751      96        1  0.056487
83     0.014393  0.014402      97        1  0.043716
6      0.015396 -0.027371      98        1  0.032635
41     0.012590  0.008172      99        1  0.020805
36     0.005515 -0.006658     100        1  0.009990

[100 rows x 5 columns], topic_info=      Category         Freq        Term        Total  loglift  logprob
term                                                                  
342    Default  4722.000000        игра  4722.000000  30.0000  30.0000
1029   Default  5726.000000        файл  5726.000000  29.0000  29.0000
26     Default  5237.000000          gt  5237.000000  28.0000  28.0000
113    Default  4718.000000    значение  4718.000000  27.0000  27.0000
1556   Default  5108.000000  устройство  5108.000000  26.0000  26.0000
972    Default  4415.000000      сервер  4415.000000  25.0000  25.0000
1734   Default  4257.00000

Можно посмотреть метрики.

In [20]:
import numpy as np

In [28]:
?lda.log_perplexity

In [57]:
lda.log_perplexity(corpus[:2000], total_docs=100)  # -31.65

-28.095375968398592

In [60]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [61]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [62]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [ ]:
coherence_model_lda.get_coherence()  # 0.47

### Разложение матриц в sklearn

In [29]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

Sklearn принимает на вход строки, поэтому склеим наши списки.

In [31]:
len(habr_texts)

3990

In [32]:
stexts = [' '.join(text) for text in habr_texts]

Сделаем матрицу слова-документы с помощью TfidfVectorizer

Добавим удаление стоп слов

In [34]:
vectorizer = TfidfVectorizer(max_features=25000, min_df=5, max_df=0.3, lowercase=False, stop_words=set(stopwords.words('russian')))
X = vectorizer.fit_transform(stexts)

Разложим её.

In [35]:
model = NMF(n_components=30)  # , solver="mu"

In [36]:
model.fit(X)

NMF(alpha=0.0, beta_loss='frobenius', init=None, l1_ratio=0.0, max_iter=200,
  n_components=30, random_state=None, shuffle=False, solver='cd',
  tol=0.0001, verbose=0)

In [37]:
def get_nmf_topics(model, n_top_words):
    
    #id слов.
    feat_names = vectorizer.get_feature_names()
    
    word_dict = {};
    for i in range(30):
        
        #топ n слов для темы.
        words_ids = model.components_[i].argsort()[:-n_top_words - 1:-1]
        words = [feat_names[key] for key in words_ids]
        word_dict['Topic # ' + '{:02d}'.format(i+1)] = words;
    
    return pd.DataFrame(word_dict);

In [38]:
get_nmf_topics(model, 10)

Topic # 01 Topic # 02 Topic # 03   Topic # 04        Topic # 05  \
0      продукт         gt       игра  космический              язык   
1       клиент         lt      игрок      спутник            объект   
2    сотрудник        div    игровой       орбита          значение   
3       бизнес      class     играть       ракета           элемент   
4  программист       name         vr         марс  программирование   
5     менеджер       html   персонаж      аппарат            строка   
6         опыт        std      steam        земля          алгоритм   
7     заказчик       type      unity         луна             текст   
8          crm       text   геймплей         наса         программа   
9       деньга      label     движок        полёт        переменный   

  Topic # 06   Topic # 07  Topic # 08 Topic # 09 Topic # 10    ...      \
0     сервер       камера          js     public       this    ...       
1     клиент   устройство         css     string      react    ...       
2         ip     смартфон  javascript        int      props    ...       
3      адрес      телефон       react         if  компонент    ...       
4     запрос  аккумулятор     angular     return   function    ...       
5      домен       датчик         веб       void        div    ...       
6     сервис        видео     браузер        new      const    ...       
7     трафик        экран         vue        amp        dom    ...       
8        dns        карта        html    private     return    ...       
9  провайдер      дисплей    страница      класс      state    ...       

   Topic # 21          Topic # 22      Topic # 23  Topic # 24    Topic # 25  \
0       товар           процессор            дата         бот        сигнал   
1      скидка                диск           центр    telegram          звук   
2     магазин              память  инфраструктура   сообщение       наушник   
3        цена               intel        облачный         чат       частота   
4  распродажа                 ssd          услуга         bot     усилитель   
5  покупатель  производительность    оборудование    телеграм     искажение   
6     покупка                ядро          облако         api      звуковой   
7     пятница          накопитель             цод  мессенджер        музыка   
8     продажа                  гб              ит       канал      диапазон   
9      чёрный                тест       провайдер     message  акустический   

  Topic # 26     Topic # 27 Topic # 28  Topic # 29 Topic # 30  
0        the             ия        php  российский        end  
1         of       обучение    symfony      страна     select  
2         to          робот        yii       рынок       from  
3        and      нейросеть    laravel       рубль         as  
4         in      интеллект       yii2      россия     запрос  
5         is  искусственный         gt      google       null  
6        for       машинный       язык       налог        set  
7         on      нейронный        psr       закон       then  
8         my       алгоритм        api       доход    таблица  
9        you       deepmind      форум         000      begin  

[10 rows x 30 columns]